In [1]:
import doctest
import random
import re
import time
import pickle
import xml.etree.ElementTree as ET
import json
import os
import sys

In [2]:
def p_equal(p1, p2):
    if len(p1) > 0 and p1[-1] == '$':
        p1 = p1[:-1]
    if len(p2) > 0 and p2[-1] == '$':
        p2 = p2[:-1]
    return p1 == p2

def p_match(p1, p2):
    if p1[-1:] == ['$']:
        if len(p1) != len(p2) or p2[-1:] != ['$']:
            return False
    else:
        if len(p1) > len(p2):
            return False
    return p1 == p2[:len(p1)]

def p_diff(p1, p2):
    for i in range(len(p1)):
        if i >= len(p2) or p1[i] != p2[i]:
            return p1[i:]
    return []

In [6]:
SIMILARITY_THRESHOLD = 5
ADD_LINK_TIME = 10000
DISCRIMINATION_TIME = 10000
FAMILIARISATION_TIME = 2000

In [7]:
class Stm:
    class Item:   #create an item container with head and pointer to next container                
        def __init__(self, data):    
            self.next = None
            self.data = data

    def __init__(self, maxlen): #STM constructor
        self.maxlen = maxlen
        self.size = 0
        self.head = None
        self.tail = None

    def push(self, data):
        self.remove(data)
        e = Stm.Item(data)
        if self.size == 0:
            self.head = self.tail = e
        else:
            check = self.head.data.image.copy()
            k = 0
            # print('check similarity', check, data.image)
            matches = []
            for i in data.image:
                if i in check:
                    k += 1
                    matches.append((data.idx, i, check))
                    if k == SIMILARITY_THRESHOLD:
                        self.head.data.similarity_links.add(data)
                        data.similarity_links.add(self.head.data)
#                         print('------------------------')
#                         for idx, i, check in matches:
#                             print(data.idx, 'FOUND', i, 'in', check)
#                         print('------------------------')
                        break
                    check.remove(i)
            self.tail.next = e
            self.tail = e
        self.size += 1
        if self.size > self.maxlen:
            self.pop()

    def pop(self):
        if self.size == 0:
            return None
        else:
            e = self.head.data
            self.head = self.head.next
            self.size -= 1
            return e

    def remove(self, value):
        if self.size == 0:
            return
        if self.head.data == value:
            self.head = self.head.next
            self.size -= 1
        else:
            p = self.head
            e = self.head.next
            while e:
                if e.data == value:
                    p.next = e.next
                    self.size -= 1
                    if e == self.tail:
                        self.tail = p
                    break
                p = p.next
                e = e.next

    class Iterator:
        def __init__(self, e):
            self.e = e

        def __next__(self):
            if self.e:
                e = self.e
                self.e = e.next
                return e.data
            raise StopIteration()

    def __iter__(self):
        return Stm.Iterator(self.head)

In [8]:
class Link:
    def __init__(self, test, child):
        self.test = test
        self.child = child
    
    def passes(self, pattern):
        return p_match(self.test, pattern)

In [9]:
class Node:
    def __init__(self, nodes, contents, image, children):
        self.contents = contents
        self.image = image
        if len(self.image) > 1 and self.image[-1] == '$':
            self.image.pop()
        self.children = children
        self.idx = len(nodes)
        nodes.append(self)
        self.label = None
        self.similarity_links = set()

In [10]:
class Modality:
    def __init__(self, chrest, name, stm_size=2):
        self.chrest = chrest
        self.name = name
        self.stm = Stm(stm_size)
        self.net = Node(nodes=chrest.nodes, contents=['ROOT NODE'], image=[], children=[])

    def recognise(self, pattern):
        current_node = self.net
        children = current_node.children
        sorted_pattern = pattern
        next_link = 0
        
        while next_link < len(children):
            link = children[next_link]
            if link.passes(sorted_pattern):
                current_node = link.child
                children = current_node.children
                next_link = 0
                sorted_pattern = p_diff(sorted_pattern, link.test)
            else:
                next_link += 1
        self.stm.push(current_node)
        return current_node
    
    def recognise_and_learn(self, pattern):
        current_node = self.recognise(pattern)
        if current_node.image != pattern:
            if current_node == self.net or \
               not p_match(current_node.image, pattern) or \
               current_node.image[-1:] == ['$']:
                current_node = self.discriminate(current_node, pattern)
            else:
                current_node = self.familiarise(current_node, pattern)
        self.stm.push(current_node)
        return current_node
    
    def get_first(self, pattern):
        fst = pattern[:1]
        if len(fst) == 0 or fst == ['$']:
            return []
        else:
            return fst
    
    def familiarise(self, node, pattern):
        new_info = self.get_first(p_diff(pattern, node.image))
        if len(new_info) == 0:
            return node
        
        retrieved_chunk = self.recognise(new_info)
        if retrieved_chunk == self.net:
            return self.learn_primitive(new_info)
        
        if node.image[:-1] == ['$']:
            node.image.pop()
        node.image += new_info
        self.chrest.clock += FAMILIARISATION_TIME
        return node
    
    def discriminate(self, node, pattern):
        new_info = p_diff(pattern, node.contents)
        
        if len(new_info) == 0 or new_info == ['$']:
            new_info = ['$']
            if self.recognise(new_info).contents == new_info:
                return self.add_test(node, new_info)
            else:
                child = Node(nodes=self.chrest.nodes, contents=new_info, image=new_info, children=[])
                self.net.children.append(Link(new_info, child))
                return child
        
        chunk = self.recognise(new_info)
        if chunk == self.net:
            return self.learn_primitive(self.get_first(new_info) or ['$'])
        elif p_match(chunk.contents, new_info):
            return self.add_test(node, chunk.contents.copy())
        else:
            return self.add_test(node, self.get_first(new_info))
            

    def add_test(self, node, pattern):
        for child in node.children:
            if child.test == pattern:
                return node
        if node == self.net:
            pat = pattern.copy()
        else:
            pat = node.contents + pattern
        child = Node(nodes=self.chrest.nodes, contents=pat, image=pat.copy(), children=[])
        node.children.append(Link(pattern, child))
        self.chrest.clock += DISCRIMINATION_TIME
        return child
    
    def learn_primitive(self, pattern):
        assert len(pattern) == 1
        child = Node(nodes=self.chrest.nodes, contents=pattern, image=[], children=[])
        self.net.children.append(Link(pattern, child))
        self.chrest.clock += DISCRIMINATION_TIME
        return child
    
    def print_tree(self, node=None, parent=[], level=0):
        if not node:
            node = self.net
        indent = '-------' * level
        contents = '< ' + ' '.join(p_diff(node.contents, parent)) + ' >'
        text = 'Node: ' + str(node.idx)
        image = '< '+ ' '.join(node.image) + ' >'
        
        string = [indent + contents, text, image]
        if node.label is not None:
            string.append('(' + str(node.label) + ')')
        if node.similarity_links:
            string.append({i.idx for i in node.similarity_links})
        print(*string)

        for child in node.children:
            self.print_tree(child.child, node.contents, level + 1)

    def print_stm(self):
        print('STM: ', end='')
        for node in self.stm:
            print(node.idx, '<', *node.image, '>', end=', ')
        print()


In [11]:
class Chrest:
    def __init__(self):
        self.nodes = []
        self.visual = Modality(self, 'visual')
        self.verbal = Modality(self, 'verbal')
        self.action = Modality(self, 'action')
        self.modalities = {
            'visual': self.visual,
            'verbal': self.verbal,
            'action': self.action,
        }
        self.clock = 0

# FILE OPS ================================================

In [13]:
"""To generate music experiment data, convert the .midi files to .musicxml (using something like Musescore) and then
convert the .musicxml to .json using code with comment
#CONVERT INDIVIDUAL FILES TO JSON
or
#CONVERT MUSIC DIRECTORY TO JSON 
This code cell is at the very bottom of the FILE OPS section
"""

'To generate music experiment data, convert the .midi files to .musicxml (using something like Musescore) and then\nconvert the .musicxml to .json using code with comment\n#CONVERT INDIVIDUAL FILES TO JSON\nor\n#CONVERT MUSIC DIRECTORY TO JSON \nThis code cell is at the very bottom of the FILE OPS section\n'

In [14]:
note_codes = {
    'C': 0,
    'D': 2,
    'E': 4,
    'F': 5,
    'G': 7,
    'A': 9,
    'B': 11
}

In [15]:
def sort_chord(a):
    if len(a) < 2:
        return 0
    octave = int(a[1])
    note = note_codes[a[0]]
    if len(a) > 2:
        if a[2] == 'M':
            note -= 1
        else:
            note += 1
    return -(octave * 12 + note)

In [16]:
print(sort_chord('A1'))
print(sort_chord('B6'))
print(sort_chord('C5'))
print(sort_chord('C5M'))
print(sort_chord('B4'))
print(sorted(['A1','B4','C5'], key = sort_chord))

-21
-83
-60
-59
-59
['C5', 'B4', 'A1']


In [141]:
notes1 = {}
# notes1["1"][-1].append([['A6']])
if 'v1' not in notes1:
    notes1['v1']=[]
notes1

{'v1': []}

In [142]:
notes2={'v1':[['A2'],['A3']],'v2':[ ['B1'],['B2'] ]}
notes2['v1'][-1].append(['A4'])
notes2

{'v1': [['A2'], ['A3', ['A4']]], 'v2': [['B1'], ['B2']]}

In [143]:
idx = {voice:0 for voice in notes2}
for voice in notes1:
    print('voice',voice)
    i = idx[voice]
    print(i)

voice v1
0


In [144]:
def get_patterns_musicxml(filepath):
    root = ET.parse(filepath).getroot()
    pattern1 = []
    pattern2 = []
    pattern3 = []
    
    
    for msr_first in root.findall('part[@id="P1"]/measure'):
        notes = {}
        types = {}
        times = {}
        for part in root.findall('part'):
            part_id = part.attrib['id']
            measure = part.find('measure[@number="' + msr_first.attrib['number'] + '"]')
            time = 0
            for elem in measure.getchildren():
                if elem.tag == 'note':
                    note = elem
                    if note.find('grace') is not None:       #*************************************GRACE NOTE KOSTYL'
                        continue
                    voice = part_id + '-' + note.find('voice').text
                    print('voice', voice)
                    print('notes', notes)
                    pitch = note.find('pitch')
                    if note.find('rest') is not None:
                        s = 'P'
                    else:
                        s = pitch.find('step').text + pitch.find('octave').text
                        alter = pitch.find('alter')
                        if alter is not None:            #***********************to do: double flat, double sharp?
                            s += 'Z' if alter.text == '1' else 'M'
                    print('s',s)
                    duration = int(note.find('duration').text)
                    if note.find('chord') is not None:
                        notes[voice][-1].append(s)
                    else:
                        if voice not in notes:
                            notes[voice] = []
                            types[voice] = []
                            times[voice] = []
                        notes[voice].append([s])
                        times[voice].append(time)
                        note_type = note.find('type')
                        if note_type is not None:
                            nt = note_type.text
                            if note.find('dot') is not None:
                                nt += ' dot'
                        else:
                            nt = '.'
                        types[voice].append(nt)
                        time += duration
                elif elem.tag == 'backup':
                    time -= int(elem.find('duration').text)
#         print('-------------------------------------------')
#         print('notes=', notes)
#         print('types=', types)
#         print('times=', times)
        
        result_notes = []
        result_times = []
        result_types = []
        
        idx = {voice: 0 for voice in notes}
        while True:
            min_time = 9999999
            for voice in times:
                i = idx[voice]
                t = times[voice]
                if i < len(t) and t[i] < min_time:
                    min_time = t[i]
            step = []
            time = []
            type_ = []
            for voice in times:
                i = idx[voice]
                t = times[voice]
                if i < len(t) and t[i] == min_time:
                    step.extend(notes[voice][i])
                    time = t[i]
                    type_ = types[voice][i]
                    idx[voice] += 1
            if step:
                while 'P' in step:
                    step.remove('P')
                if step:
                    result_notes.append(step)
                    result_times.append(time)
                    result_types.append(type_)
            else:
                break

        variant1 = []
        variant2 = []
        variant3 = []
        for i in range(len(result_notes)):
            notes = ''.join(sorted(set(result_notes[i]), key=sort_chord))
            variant1.append(notes)
            variant2.append(notes + '-' + str(result_times[i]))
            variant3.append(notes + '-' + result_types[i])
        pattern1.append(variant1)
        pattern2.append(variant2)
        pattern3.append(variant3)
    return pattern1, pattern2, pattern3 #returns the same pattern in 3 versions

In [37]:
xml_file='music_chrest/musicBig3/full_pieces/Elochka2_polyphonic.musicxml'
get_patterns_musicxml(xml_file)

voice P1-1
notes {}
s E4
voice P1-1
notes {'P1-1': [['E4']]}
s G4
voice P1-1
notes {'P1-1': [['E4', 'G4']]}
s E4M
voice P1-1
notes {'P1-1': [['E4', 'G4'], ['E4M']]}
s P
voice P1-2
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']]}
s E4
voice P1-3
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']]}
s P
voice P1-3
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P']]}
s P
voice P1-5
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P'], ['P']]}
s P
voice P1-5
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P'], ['P']], 'P1-5': [['P']]}
s P
voice P1-5
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P'], ['P']], 'P1-5': [['P'], ['P']]}
s P
voice P1-6
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P'], ['P']], 'P1-5': [['P'], ['P'], ['P']]}
s G3
voice P1-1
notes {}
s G4
voice P1-5
notes {'P1-1': [['G4']]}
s E3
voice P1-5
notes {'P1-1': [['G4']], 

E:\aSomeProgs\Conda\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: This method will be removed in future versions.  Use 'list(elem)' or iteration over elem instead.
  app.launch_new_instance()


([['G4E4', 'E4M', 'E4G3'],
  ['G4E3', 'E3'],
  ['G4E4G3', 'F4', 'E4', 'D4'],
  ['C4C3', 'C4'],
  []],
 [['G4E4-0', 'E4M-2', 'E4G3-3'],
  ['G4E3-0', 'E3-3'],
  ['G4E4G3-0', 'F4-1', 'E4-2', 'D4-3'],
  ['C4C3-0', 'C4-3'],
  []],
 [['G4E4-quarter', 'E4M-eighth', 'E4G3-eighth'],
  ['G4E3-quarter', 'E3-eighth'],
  ['G4E4G3-quarter', 'F4-eighth', 'E4-quarter', 'D4-eighth'],
  ['C4C3-half', 'C4-eighth'],
  []])

In [40]:
#debug with measure numbers
for measure_index, measure in enumerate(get_patterns_musicxml(xml_file)[0]): #[0] for pitch only variant
    print(measure_index, measure)

voice P1-1
notes {}
s E4
voice P1-1
notes {'P1-1': [['E4']]}
s G4
voice P1-1
notes {'P1-1': [['E4', 'G4']]}
s E4M
voice P1-1
notes {'P1-1': [['E4', 'G4'], ['E4M']]}
s P
voice P1-2
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']]}
s E4
voice P1-3
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']]}
s P
voice P1-3
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P']]}
s P
voice P1-5
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P'], ['P']]}
s P
voice P1-5
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P'], ['P']], 'P1-5': [['P']]}
s P
voice P1-5
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P'], ['P']], 'P1-5': [['P'], ['P']]}
s P
voice P1-6
notes {'P1-1': [['E4', 'G4'], ['E4M'], ['P']], 'P1-2': [['E4']], 'P1-3': [['P'], ['P']], 'P1-5': [['P'], ['P'], ['P']]}
s G3
voice P1-1
notes {}
s G4
voice P1-5
notes {'P1-1': [['G4']]}
s E3
voice P1-5
notes {'P1-1': [['G4']], 

E:\aSomeProgs\Conda\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: This method will be removed in future versions.  Use 'list(elem)' or iteration over elem instead.
  app.launch_new_instance()


In [15]:
for label in os.listdir('music/music_xmls/bach/wtc'):
    print(label)

WT1_1A.musicxml
WT1_1B.musicxml
WT1_2A.musicxml
WT1_2B.musicxml
WT1_3A.musicxml
WT1_3B.musicxml
WT1_4A.musicxml
WT1_4B.musicxml
WT1_5A.musicxml
WT1_5B.musicxml
WT1_6A.musicxml
WT1_6B.musicxml
WT1_7A.musicxml
WT1_7B.musicxml
WT1_8A.musicxml
WT1_8B.musicxml
WT1_9A.musicxml
WT1_9B.musicxml
WT1_X1A.musicxml
WT1_X1B.musicxml
WT1_X2A.musicxml
WT1_X2B.musicxml
WT1_X3A.musicxml
WT1_X3B.musicxml
WT1_X4A.musicxml
WT1_X4B.musicxml
WT1_X5A.musicxml
WT1_X5B.musicxml
WT1_X6A.musicxml
WT1_X6B.musicxml
WT1_X7A.musicxml
WT1_X7B.musicxml
WT1_X8A.musicxml
WT1_X8B.musicxml
WT1_X9A.musicxml
WT1_X9B.musicxml
WT1_XX1A.musicxml
WT1_XX1B.musicxml
WT1_XX2A.musicxml
WT1_XX2B.musicxml
WT1_XX3A.musicxml
WT1_XX3B.musicxml
WT1_XX4A.musicxml
WT1_XX4B.musicxml
WT1_XX_A.musicxml
WT1_XX_B.musicxml
WT1_X_A.musicxml
WT1_X_B.musicxml
Wtcii01a.musicxml
Wtcii01b.musicxml
WTCII02A.musicxml
Wtcii02b.musicxml
WTCII03A.musicxml
Wtcii03b.musicxml
WTCII04A.musicxml
Wtcii04b.musicxml
WTCII05A.musicxml
Wtcii05b.musicxml
WTCII06A.mus

In [11]:
def get_all_files(folder, end='.musicxml'):
    return tuple(os.path.join(folder, name) for name in os.listdir(folder) if name.endswith(end))

In [26]:
#CONVERT INDIVIDUAL FILES TO JSON
# files = ('full_pieces/2chop.musicxml', 'full_pieces/Elochka2.musicxml')
# save_names = ('full_pieces/2chop.json', 'full_pieces/Elochka2.json')

#CONVERT MUSIC DIRECTORY TO JSON
files = get_all_files('music/music_xmls/schumann')
#('full_pieces/Elochka3.musicxml','full_pieces/Nocturne_Op.9_No.2_Frederic_Chopin.musicxml')
save_names = tuple('music/jsons/schumann\\' + name.split('\\')[-1][:-8] + 'json' for name in files)
#('full_pieces/Elochka3.json','full_pieces/Nocturne_Op.9_No.2_Frederic_Chopin.json')

variant = 0 # 0=pure pitch; varian1=pitch+duration integer, 2=pitch+type(e.g.quarter) 
for file, save_filename in zip(files, save_names):
    print(file)
    patterns = get_patterns_musicxml(file)[variant] 
    with open(save_filename, 'w') as f:
        f.write(json.dumps(patterns))

music/music_xmls/schumann\6 Impromptus ''Bilder aus Osten'' for 4-hands op66 n1.musicxml
music/music_xmls/schumann\6 Impromptus ''Bilder aus Osten'' for 4-hands op66 n2.musicxml
music/music_xmls/schumann\6 Impromptus ''Bilder aus Osten'' for 4-hands op66 n3.musicxml
music/music_xmls/schumann\6 Impromptus ''Bilder aus Osten'' for 4-hands op66 n4.musicxml
music/music_xmls/schumann\6 Impromptus ''Bilder aus Osten'' for 4-hands op66 n5.musicxml


E:\aSomeProgs\Conda\envs\dtensor\lib\site-packages\ipykernel_launcher.py:16: DeprecationWarning: This method will be removed in future versions.  Use 'list(elem)' or iteration over elem instead.
  app.launch_new_instance()


music/music_xmls/schumann\6 Impromptus ''Bilder aus Osten'' for 4-hands op66 n6.musicxml
music/music_xmls/schumann\8 Fantaisies Kreisleriana op16.musicxml
music/music_xmls/schumann\8 Novelettes op21 n1.musicxml
music/music_xmls/schumann\8 Novelettes op21 n2.musicxml
music/music_xmls/schumann\8 Novelettes op21 n4.musicxml
music/music_xmls/schumann\Abegg Variations op1.musicxml
music/music_xmls/schumann\Album fur die Jugend op68 n01.musicxml
music/music_xmls/schumann\Album fur die Jugend op68 n05.musicxml
music/music_xmls/schumann\Album fur die Jugend op68 n06.musicxml
music/music_xmls/schumann\Album fur die Jugend op68 n07.musicxml
music/music_xmls/schumann\Album fur die Jugend op68 n14.musicxml
music/music_xmls/schumann\Album fur die Jugend op68 n18.musicxml
music/music_xmls/schumann\Album fur die Jugend op68 n19.musicxml
music/music_xmls/schumann\Concertstück for Piano and Orchestra op92.musicxml
music/music_xmls/schumann\Etude op13 n3.musicxml
music/music_xmls/schumann\Fantasiestücke

In [9]:
files = get_all_files('tests')
save_names = tuple('tests_json\\' + name.split('\\')[-1][:-8] + 'json' for name in files)

variant = 0 # 0=pure pitch; varian1=pitch+duration integer, 2=pitch+type(e.g.quarter) 
for file, save_filename in zip(files, save_names):
    print(file)
    patterns = get_patterns_musicxml(file)[variant] 
    with open(save_filename, 'w') as f:
        f.write(json.dumps(patterns))

FileNotFoundError: [WinError 3] The system cannot find the path specified: 'tests'

# TRAINING ================================================

In [41]:
sep_sent = '\.|!|\?|\.\.\.|…'
sep_phrases = '\.|!|\?|\.\.\.|…|,|:|;|-|—|"|\'|&'
sep_number = 20

In [18]:
def get_literature_patterns(text, separator, split_by_letters=None):
    patterns=[]
    if isinstance(separator, int):
        words = [word for word in re.split('[^a-zа-я]+', text.lower())]
        for i in range(0, len(words), separator):
            patterns.append(words[i:i+separator] +['$'])
    return patterns

In [19]:
file = 'testing.txt'
lf = lambda text: get_literature_patterns(text, 4)
with open(file, 'r', encoding='utf-8',errors='ignore') as f:
    patts =lf(f.read())
print(patts)

[['sing', 'o', 'goddess', 'the', '$'], ['anger', 'of', 'achilles', 'son', '$'], ['of', 'peleus', 'that', 'brought', '$'], ['countless', 'ills', 'upon', 'the', '$'], ['achaeans', 'many', 'a', 'brave', '$'], ['soul', 'did', 'it', 'send', '$'], ['hurrying', 'down', 'to', 'hades', '$'], ['and', 'many', 'a', 'hero', '$'], ['did', 'it', 'yield', 'a', '$'], ['prey', 'to', 'dogs', 'and', '$'], ['vultures', 'for', 'so', 'were', '$'], ['the', 'counsels', 'of', 'zeus', '$'], ['fulfilled', 'from', 'the', 'day', '$'], ['on', 'which', 'the', 'son', '$'], ['of', 'atreus', 'king', 'of', '$'], ['men', 'and', 'great', 'achilles', '$'], ['first', 'fell', 'out', 'with', '$'], ['one', 'another', 'and', 'which', '$'], ['of', 'the', 'gods', 'was', '$'], ['it', 'that', 'set', 'them', '$'], ['on', 'to', 'quarrel', 'it', '$'], ['was', 'the', 'son', 'of', '$'], ['zeus', '$']]


In [148]:
file = 'testing.txt'
lf = lambda text: get_literature_patterns(text, 4)
with open(file, 'r', encoding='utf-8',errors='ignore') as f:
    patts =lf(f.read())
print(patts)
    

[['sing', 'o', 'goddess', 'the', '$'], ['anger', 'of', 'achilles', 'son', '$'], ['of', 'peleus', 'that', 'brought', '$'], ['countless', 'ills', 'upon', 'the', '$'], ['achaeans', 'many', 'a', 'brave', '$'], ['soul', 'did', 'it', 'send', '$'], ['hurrying', 'down', 'to', 'hades', '$'], ['and', 'many', 'a', 'hero', '$'], ['did', 'it', 'yield', 'a', '$'], ['prey', 'to', 'dogs', 'and', '$'], ['vultures', 'for', 'so', 'were', '$'], ['the', 'counsels', 'of', 'zeus', '$'], ['fulfilled', 'from', 'the', 'day', '$'], ['on', 'which', 'the', 'son', '$'], ['of', 'atreus', 'king', 'of', '$'], ['men', 'and', 'great', 'achilles', '$'], ['first', 'fell', 'out', 'with', '$'], ['one', 'another', 'and', 'which', '$'], ['of', 'the', 'gods', 'was', '$'], ['it', 'that', 'set', 'them', '$'], ['on', 'to', 'quarrel', 'it', '$'], ['was', 'the', 'son', 'of', '$'], ['zeus', '$']]


In [149]:
some_test = 'Sing, O goddess, the anger of Achilles son of Peleus, that brought countless ills upon the Achaeans. Many a brave soul did it send hurrying down to Hades, and many a hero did it yield a prey to dogs and vultures, for so were the counsels of Zeus fulfilled from the day on which the son of Atreus, king of men, and great Achilles, first fell out with one another. And which of the gods was it that set them on to quarrel? It was the son of Zeus'
some_file_test = 'testing.txt'
with open(some_file_test, 'r') as f:
    print(f.read())
# get_literature_patterns(some_test, 5)
ltest = lambda x, y: x+y
ltest(10,20)

Sing, O goddess, the anger of Achilles son of Peleus, that brought
countless ills upon the Achaeans. Many a brave soul did it send hurrying
down to Hades, and many a hero did it yield a prey to dogs and vultures,
for so were the counsels of Zeus fulfilled from the day on which the
son of Atreus, king of men, and great Achilles, first fell out with
one another. 

And which of the gods was it that set them on to quarrel? It was the
son of Zeus


30

In [20]:
def get_sentences(text, sep, min_len=3): #number of words?
    patterns = []
    
    if isinstance(sep, int): #take sep_number words otherwise split by punctuation
        words = [word for word in re.split('[^a-zа-я]+', text.lower())] # if len(word) >= 3] #option to remove short words
        for i in range(0, len(words), sep):
            patterns.append(words[i:i + sep] + ['$'])
    else:
        for sent in re.split(sep, text.lower()):
            sent = list(filter(lambda word : len(word) >= 3, re.split('[^a-zа-я]+', sent)))
            if len(sent) >= min_len:
                patterns.append(sent + ['$'])
    return patterns

In [55]:
def train(folder, get_patterns=None): #Same as above, easier interface for multiple categories
    inp = []

    for label in os.listdir(folder):
        p = os.path.join(folder, label)
        if os.path.isdir(p):
            for file in os.listdir(p):
                file = os.path.join(p, file)
                with open(file, 'r',  encoding='utf-8', errors='ignore') as f:
                    patterns = get_patterns(f.read())
                inp += list(zip((list(p) + ['$'] for p in patterns), [[*label, '$']] * len(patterns)))
                print('inp', inp)
    
    #random.shuffle(inp) #shuffle input patterns
    chrest = Chrest() #comment out to learn on top of previous knowledge, uncomment to train from blank slate
    for i in range(3): #default 300
        errors = 0
#         if i//10==0:
        print(i, '/', 5000)
        i = 0
        n = len(inp)
        for pattern in inp:
            # print('handle pattern', i, '/', n)
            i += 1
            vis, verb = pattern
            t = chrest.clock
            node1 = chrest.visual.recognise_and_learn(vis)
            node2 = chrest.verbal.recognise_and_learn(verb)
            if chrest.clock != t:
                errors += 1
                continue
            node1.label = node2.idx
            node2.label = node1.idx
        if errors == 0:
            break
    return chrest

In [27]:
a = ["John", "Charles", "Mike"]

b = ["Jenny", "Christy", "Monica"]

x = list(zip(a, b))

#use the tuple() function to display a readable version of the result:

print(x)
label = 'man'
#zip(list(p) for p in a, label
print(a*2)
#print([label])
#print( list(zip(a, [[*label, '$']]*len(a))) )

for word in a:
	#print( list(zip(word, [[*label,'$']]*len(a)))
    print( [*word])

[('John', 'Jenny'), ('Charles', 'Christy'), ('Mike', 'Monica')]
['John', 'Charles', 'Mike', 'John', 'Charles', 'Mike']
['J', 'o', 'h', 'n']
['C', 'h', 'a', 'r', 'l', 'e', 's']
['M', 'i', 'k', 'e']


In [56]:
folder = 'testing2020/txt_simple/train_texts'
get_pats = lambda text: get_sentences(text, sep_number)

input_test = []
for label in os.listdir(folder):
    p = os.path.join(folder, label)
#     print(p, os.path.isdir(p))
    
    if os.path.isdir(p):
            for file in os.listdir(p):
                file = os.path.join(p, file)
                with open(file, 'r',  encoding='utf-8', errors='ignore') as f:
                    patterns = get_pats(f.read())
                input_test += list(zip((list(p) for p in patterns), [[*label, '$']] * len(patterns)))
print('input_test=', input_test[:2],'\n')

input_test= [(['sing', 'o', 'goddess', 'the', 'anger', 'of', 'achilles', 'son', 'of', 'peleus', 'that', 'brought', 'countless', 'ills', 'upon', 'the', 'achaeans', 'many', 'a', 'brave', '$'], ['h', 'o', 'm', 'e', 'r', '$']), (['soul', 'did', 'it', 'send', 'hurrying', 'down', 'to', 'hades', 'and', 'many', 'a', 'hero', 'did', 'it', 'yield', 'a', 'prey', 'to', 'dogs', 'and', '$'], ['h', 'o', 'm', 'e', 'r', '$'])] 



In [57]:
start = time.time()
def train_poets(folder, sep): #categorise WITHOUT using similarity links
    return train(folder, lambda text: get_sentences(text, sep))
end = time.time()
chrest = train_poets('testing2020/txt_simple/train_texts', sep_number)
print(end - start)

inp [(['sing', 'o', 'goddess', 'the', 'anger', 'of', 'achilles', 'son', 'of', 'peleus', 'that', 'brought', 'countless', 'ills', 'upon', 'the', 'achaeans', 'many', 'a', 'brave', '$', '$'], ['h', 'o', 'm', 'e', 'r', '$']), (['soul', 'did', 'it', 'send', 'hurrying', 'down', 'to', 'hades', 'and', 'many', 'a', 'hero', 'did', 'it', 'yield', 'a', 'prey', 'to', 'dogs', 'and', '$', '$'], ['h', 'o', 'm', 'e', 'r', '$']), (['vultures', 'for', 'so', 'were', 'the', 'counsels', 'of', 'zeus', 'fulfilled', 'from', 'the', 'day', 'on', 'which', 'the', 'son', 'of', 'atreus', 'king', 'of', '$', '$'], ['h', 'o', 'm', 'e', 'r', '$']), (['men', 'and', 'great', 'achilles', 'first', 'fell', 'out', 'with', 'one', 'another', 'and', 'which', 'of', 'the', 'gods', 'was', 'it', 'that', 'set', 'them', '$', '$'], ['h', 'o', 'm', 'e', 'r', '$']), (['on', 'to', 'quarrel', 'it', 'was', 'the', 'son', 'of', 'zeus', 'and', 'leto', 'for', 'he', 'was', 'angry', 'with', 'the', 'king', 'and', 'sent', '$', '$'], ['h', 'o', 'm', 

In [58]:
chrest.verbal.print_tree()

< ROOT NODE > Node: 1 <  >
-------< h > Node: 4 < h o m e r >
-------< o > Node: 7 <  >
-------< m > Node: 10 <  >
-------< e > Node: 13 <  >
-------< r > Node: 16 <  >
-------< j > Node: 136 < j o y c e > (152)
-------< y > Node: 140 <  >
-------< c > Node: 143 <  >
-------< s > Node: 153 < s h a k e s p e a r e >
-------< a > Node: 157 <  >
-------< k > Node: 159 <  >
-------< p > Node: 164 <  >


In [29]:
chrest.visual.print_tree()

< ROOT NODE > Node: 0 <  >
-------< E5G2Z > Node: 3 < E5G2Z E3 F5 B3 E5M D4 E5E4 D4 E4 B3 D5 E3 > (4)
-------< A2 > Node: 5 < A2 E3 E4 A3 C5 C4 B4E4 C4 A4 A3 E5M E3 > (4)
-------< G4G3 > Node: 6 < G4G3 F4 E4 D4 > (7)
-------< C4 > Node: 8 < C4 > (7)
-------< G4E4 > Node: 9 < G4E4 E4E3 E4 > (7)
--------------< E4 > Node: 20 < G4E4 E4 E4G3 > (7)
-------< E4E3 > Node: 13 <  >
-------< E4 > Node: 15 <  >
-------< E3 > Node: 16 <  >
-------< F4 > Node: 18 <  >
-------< E4G3 > Node: 22 <  >
-------< F5 > Node: 23 <  >
-------< A3 > Node: 24 <  >
-------< D4 > Node: 25 <  >
-------< B3 > Node: 26 <  >
-------< C5 > Node: 27 <  >
-------< E5M > Node: 28 <  >
-------< B4E4 > Node: 29 <  >
-------< E5E4 > Node: 30 <  >
-------< A4 > Node: 31 <  >
-------< D5 > Node: 32 <  >


In [61]:
f= lambda x,y: x+y
f(3,2)

5

In [59]:
start = time.time()
def train_music(folder): #categorise WITHOUT using similarity links
    return train(folder, json.loads)

chrest = train_music('testing2020/music_exp/train_json')
end = time.time()
print(end - start)

0 / 5000
1 / 5000
2 / 5000
3 / 5000
4 / 5000
5 / 5000
6 / 5000
7 / 5000
8 / 5000
9 / 5000
10 / 5000
11 / 5000
12 / 5000
13 / 5000
14 / 5000
15 / 5000
16 / 5000
17 / 5000
18 / 5000
19 / 5000
20 / 5000
21 / 5000
22 / 5000
23 / 5000
24 / 5000
25 / 5000
26 / 5000
27 / 5000
28 / 5000
29 / 5000
30 / 5000
31 / 5000
32 / 5000
33 / 5000
34 / 5000
35 / 5000
36 / 5000
37 / 5000
38 / 5000
39 / 5000
40 / 5000
41 / 5000
42 / 5000
43 / 5000
44 / 5000
45 / 5000
46 / 5000
47 / 5000
48 / 5000
49 / 5000
50 / 5000
51 / 5000
52 / 5000
53 / 5000
54 / 5000
55 / 5000
56 / 5000
57 / 5000
58 / 5000
59 / 5000
60 / 5000
61 / 5000
62 / 5000
63 / 5000
64 / 5000
65 / 5000
66 / 5000
67 / 5000
68 / 5000
69 / 5000
70 / 5000
71 / 5000
72 / 5000
73 / 5000
74 / 5000
75 / 5000
76 / 5000
77 / 5000
78 / 5000
79 / 5000
80 / 5000
81 / 5000
82 / 5000
83 / 5000
84 / 5000
85 / 5000
86 / 5000
87 / 5000
88 / 5000
89 / 5000
90 / 5000
91 / 5000
92 / 5000
93 / 5000
94 / 5000
95 / 5000
96 / 5000
97 / 5000
98 / 5000
99 / 5000
100 / 5000

# CATEGORISATION =========================================

In [153]:
def cat_file(file, get_patterns, correct_label):
    with open(file, 'r', errors='ignore') as f:
        tests = get_patterns(f.read())

    print('+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++\n')
    print('--', file, '\n')
    print('-------- MAX IMAGE METHOD -------------------------------------\n')
    t_start = time.time()
    labels = {}
    for test in tests:
        max_image = []
        label = None
        for offset in range(len(test) - 1):
            node = chrest.visual.recognise(test[offset:])
            if node.label is not None and len(node.image) > len(max_image):
                max_image = node.image
                # label = chrest.nodes[node.label].image
                labels[node.label] = labels.get(node.label, 0) + 1 #labels value = labels value (0 if none) + 1
        # print('recognises', test, 'as', max_image or None, 'label:', label, sep='\n', end='\n\n')
    
    
    

    lab_sum = sum(labels.values())
    chrest_normalised = [(k, v / lab_sum) for k, v in labels.items()]
    top = sorted(chrest_normalised, key=lambda x: -x[1])
    for x in top:
        print('%s (prob = %s)' % (''.join(chrest.nodes[x[0]].image), round(x[1], 2)))
    winner = ''.join(chrest.nodes[top[0][0]].image) if len(top) > 0 else None
    print('correct:', winner == correct_label)
    
    print('final labels scores', labels)
    print('ended in', time.time() - t_start, 'sec')

    print('-------- MAX FREQ METHOD --------\n')
    t_start = time.time()

    labels_full = {}  #scores for all labels
    for test in tests:
        labels = {}
        max_freq = 0
        max_freq_image = None
        label = None
        for offset in range(len(test) - 1):
            node = chrest.visual.recognise(test[offset:])
            if node.label:
                freq = labels.get(node.label, 0) + 1
                labels[node.label] = freq
                if freq > max_freq:
                    max_freq = freq
                    max_freq_image = node.image
                    label = node.label
        #print('recognises', test, 'as', max_freq_image, 'labels:', labels, sep='\n', end='\n\n')
        if label:
            labels_full[label] = labels_full.get(label, 0) + 1
    print('final labels scores', labels_full)

    lab_sum = sum(labels_full.values())
    chrest_normalised = [(k, v / lab_sum) for k, v in labels_full.items()]
    top = sorted(chrest_normalised, key=lambda x: -x[1])
    for x in top:
        print('%s (prob = %s)' % (''.join(chrest.nodes[x[0]].image), round(x[1], 2)))
    winnerF = ''.join(chrest.nodes[top[0][0]].image) if len(top) > 0 else None
    print('correct:', winnerF == correct_label)
    print('ended in', time.time() - t_start, 'sec')
    return winner == correct_label # winner =return winner of maxImage, winnerF = return winner of maxFreq

In [154]:
adict = {'a':30, 'z':20, 'c':10}

In [155]:
sum_all_vs=sum(adict.values())
nrmlzd = [(k, v/sum_all_vs) for k,v in adict.items()]
nrmlzd

[('a', 0.5), ('z', 0.3333333333333333), ('c', 0.16666666666666666)]

In [156]:
sum_of_values = sum(adict.values())
half_value_pairs = [(k,v / 2) for k,v in adict.items()]
num2 = [v for v in adict.values()]
print('-half_value_pairs[0][1]=', -half_value_pairs[0][1])
print('num2=', num2)
top = sorted(half_value_pairs)
print('top=', top)
top2 = sorted(half_value_pairs,key= lambda x: -x[1])
print('top2=', top2)

-half_value_pairs[0][1]= -15.0
num2= [30, 20, 10]
top= [('a', 15.0), ('c', 5.0), ('z', 10.0)]
top2= [('a', 15.0), ('z', 10.0), ('c', 5.0)]


In [157]:
def cat(folder, get_patterns):
    correct_count = 0
    total_count = 0
    for label in os.listdir(folder):
        p = os.path.join(folder, label)
        if os.path.isdir(p):
            for file in os.listdir(p):
                total_count += 1
                correct_count += cat_file(  #use cat_file function to categorise
                    file=os.path.join(p, file),
                    get_patterns=get_patterns,
                    correct_label=label
                )
    print('-' * 70)
    print('TOTAL CORRECT:', correct_count, '/', total_count)

In [41]:
def cat_poets(folder, sep): #categorise WITHOUT using similarity links
    return cat(folder, lambda text: get_sentences(text, sep))

cat_poets('testing2020/lit_exp/predict_texts', sep_number)

+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020/lit_exp/predict_texts\chaucer\canterbury_tale1.txt 

-------- MAX IMAGE METHOD -------------------------------------



KeyboardInterrupt: 

In [161]:
def cat_music(folder): #categorise WITHOUT using similarity links
    return cat(folder, json.loads)

cat_music('testing2020\music_exp\predict_json_60')

+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\bach\WTCII09A.json 

-------- MAX IMAGE METHOD -------------------------------------

bach (prob = 0.65)
bthvn (prob = 0.24)
chopin (prob = 0.05)
mozart (prob = 0.05)
correct: True
final labels scores {6: 167, 23: 62, 11: 14, 4: 13}
ended in 1.3165054321289062 sec
-------- MAX FREQ METHOD --------

final labels scores {6: 53, 23: 53}
bach (prob = 0.5)
bthvn (prob = 0.5)
correct: True
ended in 1.368342399597168 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\bach\Wtcii09b.json 

-------- MAX IMAGE METHOD -------------------------------------

bach (prob = 0.6)
bthvn (prob = 0.22)
chopin (prob = 0.11)
mozart (prob = 0.07)
correct: True
final labels scores {23: 19, 6: 51, 11: 9, 4: 6}
ended in 0.989464521408081 sec
-------- MAX FREQ METHOD --------

final labels scores {23: 12, 6: 26, 11: 3, 4: 1}
bach (prob = 0.62)
bthvn (

final labels scores {23: 24, 6: 36, 4: 1}
bach (prob = 0.59)
bthvn (prob = 0.39)
mozart (prob = 0.02)
correct: True
ended in 0.9534239768981934 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\bthvn\Piano Sonata n08 op13 1mov.json 

-------- MAX IMAGE METHOD -------------------------------------

bthvn (prob = 0.43)
bach (prob = 0.43)
chopin (prob = 0.08)
mozart (prob = 0.07)
correct: True
final labels scores {23: 261, 6: 261, 4: 41, 11: 50}
ended in 7.286535024642944 sec
-------- MAX FREQ METHOD --------

final labels scores {23: 215, 6: 144, 4: 26, 11: 18}
bthvn (prob = 0.53)
bach (prob = 0.36)
mozart (prob = 0.06)
chopin (prob = 0.04)
correct: True
ended in 7.032191753387451 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\bthvn\Piano Sonata n08 op13 3mov.json 

-------- MAX IMAGE METHOD -------------------------------------

bach (prob = 0.41)
bthvn (prob = 0.38

final labels scores {6: 69, 23: 135, 11: 12, 4: 10}
bthvn (prob = 0.6)
bach (prob = 0.31)
chopin (prob = 0.05)
mozart (prob = 0.04)
correct: True
ended in 1.851058006286621 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\bthvn\Piano Sonata n21 1movWaldstein.json 

-------- MAX IMAGE METHOD -------------------------------------

bthvn (prob = 0.44)
bach (prob = 0.33)
mozart (prob = 0.15)
chopin (prob = 0.08)
correct: True
final labels scores {23: 267, 6: 202, 4: 91, 11: 50}
ended in 11.121392250061035 sec
-------- MAX FREQ METHOD --------

final labels scores {23: 186, 6: 83, 4: 53, 11: 10}
bthvn (prob = 0.56)
bach (prob = 0.25)
mozart (prob = 0.16)
chopin (prob = 0.03)
correct: True
ended in 10.96267557144165 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\chopin\2 Polonaises op26 n1.json 

-------- MAX IMAGE METHOD -------------------------------------

mozart (p

final labels scores {4: 98, 23: 21, 6: 14, 11: 32}
mozart (prob = 0.59)
chopin (prob = 0.19)
bthvn (prob = 0.13)
bach (prob = 0.08)
correct: False
ended in 2.5910725593566895 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\chopin\Waltz op64 n1.json 

-------- MAX IMAGE METHOD -------------------------------------

mozart (prob = 0.49)
chopin (prob = 0.4)
bthvn (prob = 0.09)
bach (prob = 0.02)
correct: False
final labels scores {4: 62, 23: 11, 11: 51, 6: 2}
ended in 1.5857486724853516 sec
-------- MAX FREQ METHOD --------

final labels scores {4: 49, 23: 10, 11: 8, 6: 1}
mozart (prob = 0.72)
bthvn (prob = 0.15)
chopin (prob = 0.12)
bach (prob = 0.01)
correct: False
ended in 1.5707998275756836 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\chopin\Waltz op70 n2.json 

-------- MAX IMAGE METHOD -------------------------------------

bthvn (prob = 0.39)
mozart (prob =

final labels scores {4: 163, 11: 17, 23: 14, 6: 2}
mozart (prob = 0.83)
chopin (prob = 0.09)
bthvn (prob = 0.07)
bach (prob = 0.01)
correct: True
ended in 1.495002031326294 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\mozart\K570 Piano Sonata 3mov.json 

-------- MAX IMAGE METHOD -------------------------------------

mozart (prob = 0.72)
chopin (prob = 0.11)
bthvn (prob = 0.1)
bach (prob = 0.07)
correct: True
final labels scores {4: 163, 11: 25, 23: 22, 6: 15}
ended in 1.1269805431365967 sec
-------- MAX FREQ METHOD --------

final labels scores {4: 99, 23: 9, 11: 10, 6: 3}
mozart (prob = 0.82)
chopin (prob = 0.08)
bthvn (prob = 0.07)
bach (prob = 0.02)
correct: True
ended in 1.1389548778533936 sec
+++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++++

-- testing2020\music_exp\predict_json_60\mozart\K617 Adagio.json 

-------- MAX IMAGE METHOD -------------------------------------

bthvn (prob = 0.38)
bach (pro

In [49]:
chrest.visual.print_tree()

< ROOT NODE > Node: 0 <  >
-------< outer > Node: 3 < outer belt of burnished metal first stayed it and under this my cuirass and the belt of mail which the > (4) {1428}
-------< to > Node: 5 < to him and he >
--------------< be > Node: 258 < to be a faithful and cautious drudge and i had destined him for something better perchance i might even have > (10) {67, 522, 9995, 2220, 2612, 3477, 14294}
---------------------< you > Node: 1172 < to be you want to keep the keys yourself and give out all the things i suppose i shouldn t > (6) {2578}
---------------------< her > Node: 1330 < to be her friend i intend to be her godmother and i beg you ll call her betsey trotwood copperfield > (6) {2597, 5887}
---------------------< made > Node: 2688 < to be made without deserving it the subject of jokes between the coachman and guard as to the coach drawing > (6) {2689, 4748}
---------------------< for > Node: 3748 < to be for i have herd him o tyme and eek other speke of criseyde swich honour tha

--------------< prye > Node: 18109 < to prye and seyde nece if that i shal be deed have here a swerd and smyteth of myn heed > (12) {4348}
--------------< heven > Node: 18166 < to heven and to done considered al thing it may not be and why for shame and it were eek > (12) {10627, 10629, 459}
--------------< reste > Node: 18241 < to reste and he answerde him do we as thee leste with al the haste goodly that they mighte they > (12) {74}
--------------< paw > Node: 18270 < to paw the tissues up from the floor grunting as he stooped twice waiting for the racing special sir the > (16)
--------------< relieve > Node: 18282 < to relieve me of the charge of the horses and another stupid boor to guide me to the presence of > (10)
--------------< biwayle > Node: 18314 < to biwayle for thy proverbes may me nought avayle nor other cure canstow noon for me eek i nil not > (12)
--------------< tiptoe > Node: 18334 < to tiptoe fanned his face rapidly with the rustling tissues the professor returning 

--------------< so > Node: 7875 < now so all their praises are but prophecies of this our time all you prefiguring and for they look d > (8) {660}
--------------< is > Node: 8101 < now is moste nede for high and low with outen any drede i wol alwey thyne hestes alle kepe have > (12)
--------------< what > Node: 8632 < now what sey ye no yes yes quod he and bet wole er i go but by my trouthe i > (12) {1477}
--------------< to > Node: 8985 < now to commit to paper matter for melancholy but not unpleasing reflection others bequeath to the confidants of their bosom > (10)
--------------< purple > Node: 9388 < now purple with love s wound and maidens call it love in idleness fetch me that flower the herb i > (8) {3255}
--------------< woot > Node: 9858 < now woot i wel ther is no peril inne and of hir song right with that word she stente and > (12)
--------------< take > Node: 9992 < now take our answer unwelcome though it be to the danaans who are waiting to receive it achilles is savage >

---------------------< mine > Node: 17529 < and those mine a somebody too many and that i what evenings when the candles came and i was expected > (6)
--------------< thither > Node: 9111 < and thither over the plain in > {20824}
---------------------< over the plain > Node: 20824 < and thither over the plain in pursuit or flight if zeus again vouchsafes glory to the son of tydeus they > (4) {9112, 22098, 9111}
----------------------------< either > Node: 22098 < and thither over the plain either in flight or in pursuit i took them from the hero aeneas let our > (4) {20824, 36}
--------------< lay > Node: 9116 < and lay my saying to your heart vex me no more with this weeping and lamentation all in the cause > (4) {8488, 74, 36}
--------------< knowing > Node: 9198 < and knowing his secrets i heard that with the single exception of mr creakle tungay considered the whole establishment masters > (6)
--------------< forming > Node: 9205 < and forming her character and infusing into it som

--------------< acquiescence > Node: 17023 < my acquiescence stuck in my throat and while i was coughing to get it up my father s voice summoned > (10)
--------------< drooping > Node: 17166 < my drooping eyelids open wide looking on darkness which the blind do see save that my soul s imaginary sight > (8)
--------------< conceal > Node: 17275 < my conceal d lady to our cancell d love nurse o she says nothing sir but weeps and weeps and > (8)
--------------< insignificance > Node: 17276 < my insignificance in one word replied i i am profoundly ignorant in all these rural accomplishments then in the name > (10)
--------------< geography > Node: 17784 < my geography book said how any part of it came to be so flat but i reflected that yarmouth might > (6)
--------------< servyse > Node: 17809 < my servyse as to my lady right and chief resort with al my wit and al my diligence and i > (12)
--------------< papers > Node: 18135 < my papers yellow d with their age be scorn d like old men of l

...

-------< F5C4B3M > Node: 53993 <  >
-------< G5ZB4D4E3 > Node: 53994 <  >
-------< D6E5ZE5 > Node: 53995 <  >
-------< G5A4D4D3 > Node: 53996 <  >
-------< B5ZC5ZA4ZE4ZA3Z > Node: 53998 <  >
-------< G5D5A2 > Node: 53999 <  >
-------< C6ZF5ZD4Z > Node: 54000 <  >
-------< A6ZG6A5ZA3 > Node: 54001 <  >
-------< E5C3C2 > Node: 54002 <  >
-------< E7ZA6E3Z > Node: 54003 <  >
-------< E6ZG5ZE4ZE3Z > Node: 54004 <  >
-------< E6MC6A5F5ZE5ME4 > Node: 54006 <  >
-------< D5C5D4C4C3 > Node: 54008 <  >
-------< E6ZB5ZG5ZB3Z > Node: 54009 <  >
-------< B5G5B4B3 > Node: 54010 <  >
-------< B5G5D3 > Node: 54012 <  >
-------< D6ZG5B4 > Node: 54013 <  >
-------< E4F3D3A2F2 > Node: 54014 <  >
-------< F7ZB4 > Node: 54015 <  >
-------< A5F5C5 > Node: 54016 <  >
-------< A5ZG5E5B2 > Node: 54017 <  >
-------< C5ZC4ZB2 > Node: 54018 <  >
-------< F7ZA6C6Z > Node: 54020 <  >
-------< B4ZB3 > Node: 54021 <  >
-------< E5ZE4ZB2 > Node: 54022 <  >
-------< C6F4ZE4MG3Z > Node: 54023 <  >
-------< E7ZG6Z > Nod

-------< B6G6D6B5D5 > Node: 54610 <  >
-------< E4B3MF1Z > Node: 54611 <  >
-------< B5G5ZE5D5B4E4 > Node: 54612 <  >
-------< F5ZD5ZF3Z > Node: 54613 <  >
-------< B5ZG5D3Z > Node: 54614 <  >
-------< B4ZA4E4G3Z > Node: 54615 <  >
-------< A4G4Z > Node: 54617 <  >
-------< D5F4D4B2M > Node: 54618 <  >
-------< C6G2Z > Node: 54619 <  >
-------< A5ZE5ZD5 > Node: 54620 <  >
-------< A6E6ZB3 > Node: 54621 <  >
-------< B5D5G4D4 > Node: 54622 <  >
-------< D5ZB4F4ZB3 > Node: 54623 <  >
-------< A5E5C5E3 > Node: 54625 <  >
-------< F5D5B4D3 > Node: 54626 <  >
-------< B3ME3C3Z > Node: 54629 <  >
-------< E6ZG5B4Z > Node: 54630 <  >
-------< B5ZF5ZB4ZG3 > Node: 54631 <  >
-------< F5B4B3G3Z > Node: 54632 <  >
-------< A5E5ZD5A4D3 > Node: 54635 <  >
-------< E6B4A4 > Node: 54636 <  >
-------< G5G4E4ZG3 > Node: 54638 <  >
-------< E6ZE5ZD5B4G4 > Node: 54639 <  >
-------< C6E5E3 > Node: 54640 <  >
-------< G4E4B3MG2 > Node: 54641 <  >
-------< B5ZB2 > Node: 54642 <  >
-------< G4ZD4E3D3 > Node:

-------< E4MG3E3 > Node: 55263 <  >
-------< E6G5A4 > Node: 55264 <  >
-------< E6ZE5ZD4 > Node: 55265 <  >
-------< E6MF5ZB2 > Node: 55266 <  >
-------< B5D2 > Node: 55267 <  >
-------< G6ZB5E3Z > Node: 55268 <  >
-------< F4ZG3E3M > Node: 55269 <  >
-------< G5E5A4Z > Node: 55271 <  >
-------< F6D6F5D5A4D4A3D3 > Node: 55272 <  >
-------< B5ZE5E4G3 > Node: 55273 <  >
-------< E6E5A3A2 > Node: 55274 <  >
-------< C6E5B2 > Node: 55275 <  >
-------< E6ZA5ZD5A4Z > Node: 55278 <  >
-------< F6ZD5ZB3 > Node: 55279 <  >
-------< B4G4ZB2 > Node: 55280 <  >
-------< F6ZD6B5F5ZF3ZF2Z > Node: 55281 <  >
-------< A4G3B2 > Node: 55282 <  >
-------< E7E6D5E4 > Node: 55283 <  >
-------< G6ZD4E3 > Node: 55284 <  >
-------< C5ZA4G4 > Node: 55285 <  >
-------< G5C5A4 > Node: 55286 <  >
-------< E7G6B3Z > Node: 55287 <  >
-------< E6ZC3Z > Node: 55289 <  >
-------< A4E4ZA3 > Node: 55290 <  >
-------< E5MA4F3Z > Node: 55292 <  >
-------< F4ZB3G3 > Node: 55293 <  >
-------< A5ZG3Z > Node: 55294 <  >
-----

-------< G6A5ZG3 > Node: 55964 <  >
-------< D5G4E4ZB3Z > Node: 55967 <  >
-------< G4C4ZE2 > Node: 55969 <  >
-------< E6ZA5ZG5 > Node: 55973 <  >
-------< F5D5A4E3 > Node: 55974 <  >
-------< E4MF3 > Node: 55976 <  >
-------< G4E3C3Z > Node: 55977 <  >
-------< B5MF5B4MF4D4D3 > Node: 55978 <  >
-------< F5G4D4B3M > Node: 55979 <  >
-------< A6A5C3ZC2Z > Node: 55980 <  >
-------< G6ZB5ZG4G3 > Node: 55981 <  >
-------< A6A5D5 > Node: 55982 <  >
-------< E5B4ZA4F4Z > Node: 55984 <  >
-------< D5ZA4E3Z > Node: 55985 <  >
-------< G6D6ZG2 > Node: 55986 <  >
-------< A6ZE5C5Z > Node: 55987 <  >
-------< D5ZG4ZD4Z > Node: 55988 <  >
-------< B4A4D4 > Node: 55989 <  >
-------< F4ZA3B2 > Node: 55990 <  >
-------< B5ZB4ZD4 > Node: 55992 <  >
-------< G5ZG4ZA3A2 > Node: 55993 <  >
-------< D6ZA5ZG5D5ZG4 > Node: 55994 <  >
-------< C7ZE6Z > Node: 55995 <  >
-------< C5ZB1 > Node: 55996 <  >
-------< D6ZA5D4 > Node: 55999 <  >
-------< F5E4G3 > Node: 56000 <  >
-------< E6ZB5ZA5E5ZA4D4 > Node: 56

-------< E6G5A4Z > Node: 56718 <  >
-------< B7ZB6ZF3Z > Node: 56719 <  >
-------< E6MB3MB2M > Node: 56720 <  >
-------< F5ZC2 > Node: 56722 <  >
-------< B7D7 > Node: 56723 <  >
-------< A6F5 > Node: 56724 <  >
-------< D7ZA6ZB5ZA5Z > Node: 56727 <  >
-------< E5ZB4A4 > Node: 56728 <  >
-------< A6G6A5G5C4Z > Node: 56729 <  >
-------< D7ZE4 > Node: 56731 <  >
-------< G5E4MA3 > Node: 56733 <  >
-------< D7E4 > Node: 56734 <  >
-------< D2Z > Node: 56735 <  >
-------< E6A5F5ZE5 > Node: 56737 <  >
-------< E6D6 > Node: 56744 <  >
-------< F3ZB1 > Node: 56745 <  >
-------< F6F5A4 > Node: 56747 <  >
-------< D6B5ZD5 > Node: 56750 <  >
-------< G5F4E4M > Node: 56752 <  >
-------< C6ZG5ZC5ZG4ZB3Z > Node: 56754 <  >
-------< C7ZC6ZF4ZF3Z > Node: 56755 <  >
-------< A4E4ZD4 > Node: 56756 <  >
-------< G6B5ZB4Z > Node: 56758 <  >
-------< B4A4C3 > Node: 56763 <  >
-------< A5ZF5ZB4Z > Node: 56765 <  >
-------< G6A5ZA4Z > Node: 56767 <  >
-------< E6B5ZA5E5Z > Node: 56771 <  >
-------< A6B5ZE4Z

In [48]:
chrest.verbal.print_tree()

< ROOT NODE > Node: 1 <  >
-------< h > Node: 4 < h o m e r > (12478)
-------< d > Node: 6 < d i c k e n s > (12471)
-------< s > Node: 8 < s h a k e s p e a r e > (12481)
-------< w > Node: 10 < w s c o t t > (12472)
-------< c > Node: 12 < c h a u c e r > (12480)
--------------< h > Node: 34918 < c h o p i n > (44853)
-------< j > Node: 16 < j o y c e > (12475)
-------< i > Node: 18 <  >
-------< a > Node: 24 <  >
-------< o > Node: 29 <  >
-------< y > Node: 35 <  >
-------< u > Node: 40 <  >
-------< m > Node: 42 < m o z a r t > (44851)
-------< k > Node: 45 <  >
-------< e > Node: 49 <  >
-------< n > Node: 58 <  >
-------< t > Node: 66 <  >
-------< p > Node: 68 <  >
-------< r > Node: 73 <  >
-------< b > Node: 34922 < b a c h > (44852)
--------------< t > Node: 34930 < b t h v n > (36171)
-------< z > Node: 34932 <  >
-------< v > Node: 34942 <  >


__No of nodes/(extrinsic)chunks in the network:__

In [21]:
len(chrest.nodes) #NUMBER of NODES  IN CHREST

34900